In [3]:
import tensorflow.compat.v1 as tf
tf.disable_v2_behavior()
import numpy as np
import matplotlib.pyplot as plt

In [5]:
#MInst 데이터 다운!! 
from tensorflow.examples.tutorials.mnist import input_data
mnist = input_data.read_data_sets("MNIST_data/", one_hot=True)

Extracting MNIST_data/train-images-idx3-ubyte.gz
Extracting MNIST_data/train-labels-idx1-ubyte.gz
Extracting MNIST_data/t10k-images-idx3-ubyte.gz
Extracting MNIST_data/t10k-labels-idx1-ubyte.gz


In [8]:
#변수 선언
learning_rate_RMSProp = 0.02
learning_rate_GradientDescent = 0.5
num_epochs = 100
batch_size = 256
input_size = 784
hidden1_size = 128
hidden2_size = 64
display_step = 1

In [9]:
x = tf.placeholder(tf.float32 , shape=[None , input_size])
y = tf.placeholder(tf.float32 , shape=[None,10])

In [11]:
def build_autoencoder(x):
    #인코딩
    Wh1 = tf.Variable(tf.random_normal(shape=[input_size,hidden1_size]))
    bh1 = tf.Variable(tf.random_normal(shape=[hidden1_size]))
    H1_output = tf.nn.sigmoid(tf.matmul(x,Wh1)+bh1)
    Wh2 = tf.Variable(tf.random_normal(shape=[hidden1_size,hidden2_size]))
    bh2 = tf.Variable(tf.random_normal(shape=[hidden2_size]))
    H2_output = tf.nn.sigmoid(tf.matmul(H1_output,Wh2)+bh2)
    #디코딩
    Wh3 = tf.Variable(tf.random_normal(shape=[hidden2_size,hidden1_size]))
    bh3 = tf.Variable(tf.random_normal(shape=[hidden1_size]))
    H3_output = tf.nn.sigmoid(tf.matmul(H2_output,Wh3)+bh3)
    Wo = tf.Variable(tf.random_normal(shape=[hidden1_size,input_size]))
    bo = tf.Variable(tf.random_normal(shape=[input_size]))
    x_reconstructed = tf.nn.sigmoid(tf.matmul(H3_output,Wo)+bo)
    return x_reconstructed,H2_output

In [23]:
def build_softmax_classifier(x):
    W_softmax = tf.Variable(tf.zeros([hidden2_size,10]))
    b_softmax = tf.Variable(tf.zeros([10]))
    y_pred = tf.nn.softmax(tf.matmul(x,W_softmax)+b_softmax)
    return y_pred

In [24]:
y_pred , extracted_features = build_autoencoder(x)
y_true = x
y_pred_softmax = build_softmax_classifier(extracted_features)

In [29]:
pretraining_cost = tf.reduce_mean(tf.pow(y_true - y_pred,2))
pretraining_train_step = tf.train.RMSPropOptimizer(learning_rate_GradientDescent).minimize(pretraining_cost)
finetuning_cost = tf.reduce_mean(-tf.reduce_sum(y*tf.log(y_pred_softmax),reduction_indices=[1]))
finetuning_train_step = tf.train.GradientDescentOptimizer(learning_rate_GradientDescent).minimize(pretraining_cost)

In [30]:
with tf.Session() as sess:
    sess.run(tf.global_variables_initializer())
    total_batch = int(mnist.train.num_examples/batch_size)
    for step in range(num_epochs):
        for i in range(total_batch):
            batch_xs , batch_ys = mnist.train.next_batch(batch_size)
            _,pretraining_loss_print = sess.run([pretraining_train_step,pretraining_cost],feed_dict={x:batch_xs})
            if step % display_step == 0:
                print("반복(step) : %d ,pre-Training 손실함수(cost) : %f"%((step+1),pretraining_loss_print))
                print("Step1 : Mnist 데이터 재구축을 위한 오토인코거 최적화 완료!!")
    for step in range(num_epochs+10):
        for i in range(total_batch):
            batch_xs , batch_ys = mnist.train.next_batch(batch_size)
            _,finetuning_loss_print = sess.run([finetuning_train_step,finetuning_cost],feed_dict={x:batch_xs,y:batch_ys})
            if step % display_step == 0:
                print("반복(step) : %d ,pre-Training 손실함수(cost) : %f"%((step+1),finetuning_loss_print))
                print("Step2 : Mnist 데이터 재구축을 위한 오토인코거 최적화 완료 + softmax 분류기 최적화 완료(Fine Tuning)!!")

    correct_prediction = tf.equal(tf.argmax(y,1),tf.argmax(y_pred_softmax,1))
    accuracy = tf.reduce_mean(tf.cast(correct_prediction,tf.float32))
    print("정확도(오토인코거 + Softmax 분류기): %f"%sess.run(accuracy,feed_dict={x:mnist.test.images,y:mnist.test.labels}))

반복(step) : 1 ,pre-Training 손실함수(cost) : 0.451334
Step1 : Mnist 데이터 재구축을 위한 오토인코거 최적화 완료!!
반복(step) : 1 ,pre-Training 손실함수(cost) : 0.450145
Step1 : Mnist 데이터 재구축을 위한 오토인코거 최적화 완료!!
반복(step) : 1 ,pre-Training 손실함수(cost) : 0.449609
Step1 : Mnist 데이터 재구축을 위한 오토인코거 최적화 완료!!
반복(step) : 1 ,pre-Training 손실함수(cost) : 0.450113
Step1 : Mnist 데이터 재구축을 위한 오토인코거 최적화 완료!!
반복(step) : 1 ,pre-Training 손실함수(cost) : 0.449213
Step1 : Mnist 데이터 재구축을 위한 오토인코거 최적화 완료!!
반복(step) : 1 ,pre-Training 손실함수(cost) : 0.449086
Step1 : Mnist 데이터 재구축을 위한 오토인코거 최적화 완료!!
반복(step) : 1 ,pre-Training 손실함수(cost) : 0.448731
Step1 : Mnist 데이터 재구축을 위한 오토인코거 최적화 완료!!
반복(step) : 1 ,pre-Training 손실함수(cost) : 0.447678
Step1 : Mnist 데이터 재구축을 위한 오토인코거 최적화 완료!!
반복(step) : 1 ,pre-Training 손실함수(cost) : 0.447853
Step1 : Mnist 데이터 재구축을 위한 오토인코거 최적화 완료!!
반복(step) : 1 ,pre-Training 손실함수(cost) : 0.447525
Step1 : Mnist 데이터 재구축을 위한 오토인코거 최적화 완료!!
반복(step) : 1 ,pre-Training 손실함수(cost) : 0.447256
Step1 : Mnist 데이터 재구축을 위한 오토인코거 최적화 완료!!
반복(step) :

반복(step) : 1 ,pre-Training 손실함수(cost) : 0.203425
Step1 : Mnist 데이터 재구축을 위한 오토인코거 최적화 완료!!
반복(step) : 1 ,pre-Training 손실함수(cost) : 0.204615
Step1 : Mnist 데이터 재구축을 위한 오토인코거 최적화 완료!!
반복(step) : 1 ,pre-Training 손실함수(cost) : 0.204746
Step1 : Mnist 데이터 재구축을 위한 오토인코거 최적화 완료!!
반복(step) : 1 ,pre-Training 손실함수(cost) : 0.204590
Step1 : Mnist 데이터 재구축을 위한 오토인코거 최적화 완료!!
반복(step) : 1 ,pre-Training 손실함수(cost) : 0.202163
Step1 : Mnist 데이터 재구축을 위한 오토인코거 최적화 완료!!
반복(step) : 1 ,pre-Training 손실함수(cost) : 0.201052
Step1 : Mnist 데이터 재구축을 위한 오토인코거 최적화 완료!!
반복(step) : 1 ,pre-Training 손실함수(cost) : 0.200351
Step1 : Mnist 데이터 재구축을 위한 오토인코거 최적화 완료!!
반복(step) : 1 ,pre-Training 손실함수(cost) : 0.201004
Step1 : Mnist 데이터 재구축을 위한 오토인코거 최적화 완료!!
반복(step) : 1 ,pre-Training 손실함수(cost) : 0.199455
Step1 : Mnist 데이터 재구축을 위한 오토인코거 최적화 완료!!
반복(step) : 1 ,pre-Training 손실함수(cost) : 0.199549
Step1 : Mnist 데이터 재구축을 위한 오토인코거 최적화 완료!!
반복(step) : 1 ,pre-Training 손실함수(cost) : 0.199839
Step1 : Mnist 데이터 재구축을 위한 오토인코거 최적화 완료!!
반복(step) :

반복(step) : 2 ,pre-Training 손실함수(cost) : 0.158673
Step1 : Mnist 데이터 재구축을 위한 오토인코거 최적화 완료!!
반복(step) : 2 ,pre-Training 손실함수(cost) : 0.153199
Step1 : Mnist 데이터 재구축을 위한 오토인코거 최적화 완료!!
반복(step) : 2 ,pre-Training 손실함수(cost) : 0.150793
Step1 : Mnist 데이터 재구축을 위한 오토인코거 최적화 완료!!
반복(step) : 2 ,pre-Training 손실함수(cost) : 0.152318
Step1 : Mnist 데이터 재구축을 위한 오토인코거 최적화 완료!!
반복(step) : 2 ,pre-Training 손실함수(cost) : 0.152105
Step1 : Mnist 데이터 재구축을 위한 오토인코거 최적화 완료!!
반복(step) : 2 ,pre-Training 손실함수(cost) : 0.153473
Step1 : Mnist 데이터 재구축을 위한 오토인코거 최적화 완료!!
반복(step) : 2 ,pre-Training 손실함수(cost) : 0.151673
Step1 : Mnist 데이터 재구축을 위한 오토인코거 최적화 완료!!
반복(step) : 2 ,pre-Training 손실함수(cost) : 0.154977
Step1 : Mnist 데이터 재구축을 위한 오토인코거 최적화 완료!!
반복(step) : 2 ,pre-Training 손실함수(cost) : 0.151574
Step1 : Mnist 데이터 재구축을 위한 오토인코거 최적화 완료!!
반복(step) : 2 ,pre-Training 손실함수(cost) : 0.153991
Step1 : Mnist 데이터 재구축을 위한 오토인코거 최적화 완료!!
반복(step) : 2 ,pre-Training 손실함수(cost) : 0.151499
Step1 : Mnist 데이터 재구축을 위한 오토인코거 최적화 완료!!
반복(step) :

반복(step) : 2 ,pre-Training 손실함수(cost) : 0.148593
Step1 : Mnist 데이터 재구축을 위한 오토인코거 최적화 완료!!
반복(step) : 2 ,pre-Training 손실함수(cost) : 0.150593
Step1 : Mnist 데이터 재구축을 위한 오토인코거 최적화 완료!!
반복(step) : 2 ,pre-Training 손실함수(cost) : 0.151061
Step1 : Mnist 데이터 재구축을 위한 오토인코거 최적화 완료!!
반복(step) : 2 ,pre-Training 손실함수(cost) : 0.150172
Step1 : Mnist 데이터 재구축을 위한 오토인코거 최적화 완료!!
반복(step) : 2 ,pre-Training 손실함수(cost) : 0.148919
Step1 : Mnist 데이터 재구축을 위한 오토인코거 최적화 완료!!
반복(step) : 2 ,pre-Training 손실함수(cost) : 0.147685
Step1 : Mnist 데이터 재구축을 위한 오토인코거 최적화 완료!!
반복(step) : 2 ,pre-Training 손실함수(cost) : 0.151915
Step1 : Mnist 데이터 재구축을 위한 오토인코거 최적화 완료!!
반복(step) : 2 ,pre-Training 손실함수(cost) : 0.153404
Step1 : Mnist 데이터 재구축을 위한 오토인코거 최적화 완료!!
반복(step) : 2 ,pre-Training 손실함수(cost) : 0.151579
Step1 : Mnist 데이터 재구축을 위한 오토인코거 최적화 완료!!
반복(step) : 2 ,pre-Training 손실함수(cost) : 0.150203
Step1 : Mnist 데이터 재구축을 위한 오토인코거 최적화 완료!!
반복(step) : 2 ,pre-Training 손실함수(cost) : 0.151691
Step1 : Mnist 데이터 재구축을 위한 오토인코거 최적화 완료!!
반복(step) :

반복(step) : 2 ,pre-Training 손실함수(cost) : 0.149640
Step1 : Mnist 데이터 재구축을 위한 오토인코거 최적화 완료!!
반복(step) : 2 ,pre-Training 손실함수(cost) : 0.151705
Step1 : Mnist 데이터 재구축을 위한 오토인코거 최적화 완료!!
반복(step) : 2 ,pre-Training 손실함수(cost) : 0.150161
Step1 : Mnist 데이터 재구축을 위한 오토인코거 최적화 완료!!
반복(step) : 2 ,pre-Training 손실함수(cost) : 0.151472
Step1 : Mnist 데이터 재구축을 위한 오토인코거 최적화 완료!!
반복(step) : 2 ,pre-Training 손실함수(cost) : 0.152410
Step1 : Mnist 데이터 재구축을 위한 오토인코거 최적화 완료!!
반복(step) : 2 ,pre-Training 손실함수(cost) : 0.152796
Step1 : Mnist 데이터 재구축을 위한 오토인코거 최적화 완료!!
반복(step) : 2 ,pre-Training 손실함수(cost) : 0.151871
Step1 : Mnist 데이터 재구축을 위한 오토인코거 최적화 완료!!
반복(step) : 2 ,pre-Training 손실함수(cost) : 0.150832
Step1 : Mnist 데이터 재구축을 위한 오토인코거 최적화 완료!!
반복(step) : 2 ,pre-Training 손실함수(cost) : 0.151572
Step1 : Mnist 데이터 재구축을 위한 오토인코거 최적화 완료!!
반복(step) : 3 ,pre-Training 손실함수(cost) : 0.150726
Step1 : Mnist 데이터 재구축을 위한 오토인코거 최적화 완료!!
반복(step) : 3 ,pre-Training 손실함수(cost) : 0.151693
Step1 : Mnist 데이터 재구축을 위한 오토인코거 최적화 완료!!
반복(step) :

...

반복(step) : 109 ,pre-Training 손실함수(cost) : 2.302585
Step2 : Mnist 데이터 재구축을 위한 오토인코거 최적화 완료 + softmax 분류기 최적화 완료(Fine Tuning)!!
반복(step) : 109 ,pre-Training 손실함수(cost) : 2.302585
Step2 : Mnist 데이터 재구축을 위한 오토인코거 최적화 완료 + softmax 분류기 최적화 완료(Fine Tuning)!!
반복(step) : 109 ,pre-Training 손실함수(cost) : 2.302585
Step2 : Mnist 데이터 재구축을 위한 오토인코거 최적화 완료 + softmax 분류기 최적화 완료(Fine Tuning)!!
반복(step) : 109 ,pre-Training 손실함수(cost) : 2.302585
Step2 : Mnist 데이터 재구축을 위한 오토인코거 최적화 완료 + softmax 분류기 최적화 완료(Fine Tuning)!!
반복(step) : 109 ,pre-Training 손실함수(cost) : 2.302585
Step2 : Mnist 데이터 재구축을 위한 오토인코거 최적화 완료 + softmax 분류기 최적화 완료(Fine Tuning)!!
반복(step) : 109 ,pre-Training 손실함수(cost) : 2.302585
Step2 : Mnist 데이터 재구축을 위한 오토인코거 최적화 완료 + softmax 분류기 최적화 완료(Fine Tuning)!!
반복(step) : 109 ,pre-Training 손실함수(cost) : 2.302585
Step2 : Mnist 데이터 재구축을 위한 오토인코거 최적화 완료 + softmax 분류기 최적화 완료(Fine Tuning)!!
반복(step) : 109 ,pre-Training 손실함수(cost) : 2.302585
Step2 : Mnist 데이터 재구축을 위한 오토인코거 최적화 완료 + softmax 분류기 최적화 완료(Fine Tu

반복(step) : 109 ,pre-Training 손실함수(cost) : 2.302585
Step2 : Mnist 데이터 재구축을 위한 오토인코거 최적화 완료 + softmax 분류기 최적화 완료(Fine Tuning)!!
반복(step) : 109 ,pre-Training 손실함수(cost) : 2.302585
Step2 : Mnist 데이터 재구축을 위한 오토인코거 최적화 완료 + softmax 분류기 최적화 완료(Fine Tuning)!!
반복(step) : 109 ,pre-Training 손실함수(cost) : 2.302585
Step2 : Mnist 데이터 재구축을 위한 오토인코거 최적화 완료 + softmax 분류기 최적화 완료(Fine Tuning)!!
반복(step) : 109 ,pre-Training 손실함수(cost) : 2.302585
Step2 : Mnist 데이터 재구축을 위한 오토인코거 최적화 완료 + softmax 분류기 최적화 완료(Fine Tuning)!!
반복(step) : 109 ,pre-Training 손실함수(cost) : 2.302585
Step2 : Mnist 데이터 재구축을 위한 오토인코거 최적화 완료 + softmax 분류기 최적화 완료(Fine Tuning)!!
반복(step) : 109 ,pre-Training 손실함수(cost) : 2.302585
Step2 : Mnist 데이터 재구축을 위한 오토인코거 최적화 완료 + softmax 분류기 최적화 완료(Fine Tuning)!!
반복(step) : 109 ,pre-Training 손실함수(cost) : 2.302585
Step2 : Mnist 데이터 재구축을 위한 오토인코거 최적화 완료 + softmax 분류기 최적화 완료(Fine Tuning)!!
반복(step) : 109 ,pre-Training 손실함수(cost) : 2.302585
Step2 : Mnist 데이터 재구축을 위한 오토인코거 최적화 완료 + softmax 분류기 최적화 완료(Fine Tu

반복(step) : 110 ,pre-Training 손실함수(cost) : 2.302585
Step2 : Mnist 데이터 재구축을 위한 오토인코거 최적화 완료 + softmax 분류기 최적화 완료(Fine Tuning)!!
반복(step) : 110 ,pre-Training 손실함수(cost) : 2.302585
Step2 : Mnist 데이터 재구축을 위한 오토인코거 최적화 완료 + softmax 분류기 최적화 완료(Fine Tuning)!!
반복(step) : 110 ,pre-Training 손실함수(cost) : 2.302585
Step2 : Mnist 데이터 재구축을 위한 오토인코거 최적화 완료 + softmax 분류기 최적화 완료(Fine Tuning)!!
반복(step) : 110 ,pre-Training 손실함수(cost) : 2.302585
Step2 : Mnist 데이터 재구축을 위한 오토인코거 최적화 완료 + softmax 분류기 최적화 완료(Fine Tuning)!!
반복(step) : 110 ,pre-Training 손실함수(cost) : 2.302585
Step2 : Mnist 데이터 재구축을 위한 오토인코거 최적화 완료 + softmax 분류기 최적화 완료(Fine Tuning)!!
반복(step) : 110 ,pre-Training 손실함수(cost) : 2.302585
Step2 : Mnist 데이터 재구축을 위한 오토인코거 최적화 완료 + softmax 분류기 최적화 완료(Fine Tuning)!!
반복(step) : 110 ,pre-Training 손실함수(cost) : 2.302585
Step2 : Mnist 데이터 재구축을 위한 오토인코거 최적화 완료 + softmax 분류기 최적화 완료(Fine Tuning)!!
반복(step) : 110 ,pre-Training 손실함수(cost) : 2.302585
Step2 : Mnist 데이터 재구축을 위한 오토인코거 최적화 완료 + softmax 분류기 최적화 완료(Fine Tu

반복(step) : 110 ,pre-Training 손실함수(cost) : 2.302585
Step2 : Mnist 데이터 재구축을 위한 오토인코거 최적화 완료 + softmax 분류기 최적화 완료(Fine Tuning)!!
반복(step) : 110 ,pre-Training 손실함수(cost) : 2.302585
Step2 : Mnist 데이터 재구축을 위한 오토인코거 최적화 완료 + softmax 분류기 최적화 완료(Fine Tuning)!!
반복(step) : 110 ,pre-Training 손실함수(cost) : 2.302585
Step2 : Mnist 데이터 재구축을 위한 오토인코거 최적화 완료 + softmax 분류기 최적화 완료(Fine Tuning)!!
반복(step) : 110 ,pre-Training 손실함수(cost) : 2.302585
Step2 : Mnist 데이터 재구축을 위한 오토인코거 최적화 완료 + softmax 분류기 최적화 완료(Fine Tuning)!!
반복(step) : 110 ,pre-Training 손실함수(cost) : 2.302585
Step2 : Mnist 데이터 재구축을 위한 오토인코거 최적화 완료 + softmax 분류기 최적화 완료(Fine Tuning)!!
반복(step) : 110 ,pre-Training 손실함수(cost) : 2.302585
Step2 : Mnist 데이터 재구축을 위한 오토인코거 최적화 완료 + softmax 분류기 최적화 완료(Fine Tuning)!!
반복(step) : 110 ,pre-Training 손실함수(cost) : 2.302585
Step2 : Mnist 데이터 재구축을 위한 오토인코거 최적화 완료 + softmax 분류기 최적화 완료(Fine Tuning)!!
반복(step) : 110 ,pre-Training 손실함수(cost) : 2.302585
Step2 : Mnist 데이터 재구축을 위한 오토인코거 최적화 완료 + softmax 분류기 최적화 완료(Fine Tu

반복(step) : 110 ,pre-Training 손실함수(cost) : 2.302585
Step2 : Mnist 데이터 재구축을 위한 오토인코거 최적화 완료 + softmax 분류기 최적화 완료(Fine Tuning)!!
반복(step) : 110 ,pre-Training 손실함수(cost) : 2.302585
Step2 : Mnist 데이터 재구축을 위한 오토인코거 최적화 완료 + softmax 분류기 최적화 완료(Fine Tuning)!!
반복(step) : 110 ,pre-Training 손실함수(cost) : 2.302585
Step2 : Mnist 데이터 재구축을 위한 오토인코거 최적화 완료 + softmax 분류기 최적화 완료(Fine Tuning)!!
반복(step) : 110 ,pre-Training 손실함수(cost) : 2.302585
Step2 : Mnist 데이터 재구축을 위한 오토인코거 최적화 완료 + softmax 분류기 최적화 완료(Fine Tuning)!!
반복(step) : 110 ,pre-Training 손실함수(cost) : 2.302585
Step2 : Mnist 데이터 재구축을 위한 오토인코거 최적화 완료 + softmax 분류기 최적화 완료(Fine Tuning)!!
반복(step) : 110 ,pre-Training 손실함수(cost) : 2.302585
Step2 : Mnist 데이터 재구축을 위한 오토인코거 최적화 완료 + softmax 분류기 최적화 완료(Fine Tuning)!!
반복(step) : 110 ,pre-Training 손실함수(cost) : 2.302585
Step2 : Mnist 데이터 재구축을 위한 오토인코거 최적화 완료 + softmax 분류기 최적화 완료(Fine Tuning)!!
반복(step) : 110 ,pre-Training 손실함수(cost) : 2.302585
Step2 : Mnist 데이터 재구축을 위한 오토인코거 최적화 완료 + softmax 분류기 최적화 완료(Fine Tu